# Rival Rush - EDA

In [2]:
pip install -r requirements.txt

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
from pathlib import Path
import sys
import json
from typing import List, Dict, Union, Any  # Importiere Any

In [4]:
import os
from pathlib import Path

def zeige_ordnerstruktur(ordner_pfad: str, einrueckung: str = "") -> None:
    """
    Zeigt die Ordnerstruktur rekursiv an, beginnend bei einem gegebenen Pfad.

    Args:
        ordner_pfad: Der Pfad des Ordners, dessen Struktur angezeigt werden soll.
        einrueckung: Ein String, der für die Einrückung der Ausgabe verwendet wird (für die Rekursion).
    """
    pfad = Path(ordner_pfad)

    if not pfad.is_dir():
        print(f"Fehler: Der Pfad '{ordner_pfad}' ist kein gültiger Ordner.")
        return

    print(einrueckung + pfad.name + "/")  # Ordnernamen mit Schrägstrich kennzeichnen
    einrueckung += "  "  # Einrückung für die nächste Ebene erhöhen

    # Dateien und Unterordner im aktuellen Ordner auflisten
    inhalte = sorted(pfad.iterdir()) # sortiert, damit die Ausgabe reproduzierbar ist.
    for inhalt in inhalte:
        if inhalt.is_dir():
            # Rekursiver Aufruf für Unterordner
            zeige_ordnerstruktur(str(inhalt), einrueckung)
        else:
            # Dateien ohne Schrägstrich ausgeben
            print(einrueckung + inhalt.name)

# --- Beispielaufruf ---
# Ersetze 'Replays/Replay Data/' durch den Pfad, dessen Struktur du sehen möchtest
ordner_pfad = 'Replays/Replay Data/'
zeige_ordnerstruktur(ordner_pfad)


Replay Data/
  76561197960320249_DrunKingan/
    replay_data_76561197960320249_1.json
    replay_data_76561197960320249_10.json
    replay_data_76561197960320249_11.json
    replay_data_76561197960320249_12.json
    replay_data_76561197960320249_13.json
    replay_data_76561197960320249_14.json
    replay_data_76561197960320249_15.json
    replay_data_76561197960320249_16.json
    replay_data_76561197960320249_17.json
    replay_data_76561197960320249_18.json
    replay_data_76561197960320249_19.json
    replay_data_76561197960320249_2.json
    replay_data_76561197960320249_20.json
    replay_data_76561197960320249_21.json
    replay_data_76561197960320249_22.json
    replay_data_76561197960320249_23.json
    replay_data_76561197960320249_24.json
    replay_data_76561197960320249_25.json
    replay_data_76561197960320249_26.json
    replay_data_76561197960320249_27.json
    replay_data_76561197960320249_28.json
    replay_data_76561197960320249_29.json
    replay_data_76561197960320249

In [5]:


def lese_json_datei(pfad: str) -> Union[Dict, None]:
    """
    Liest eine JSON-Datei und gibt den Inhalt als Dictionary zurück.
    Behandelt Fehler beim Lesen der Datei.

    Args:
        pfad (str): Der Pfad zur JSON-Datei.

    Returns:
        Union[Dict, None]: Der Inhalt der JSON-Datei als Dictionary, oder None bei Fehler.
    """
    try:
        with open(pfad, 'r', encoding='utf-8') as f:
            return json.load(f)
    except (FileNotFoundError, json.JSONDecodeError) as e:
        print(f"Fehler beim Lesen der JSON-Datei '{pfad}': {e}")
        return None

def extrahiere_daten(daten: Dict) -> Union[Dict, None]:
    """
    Extrahiert die relevanten Daten aus dem geladenen JSON-Dictionary,
    indem es rekursiv durch die Struktur geht.  Gibt None zurück, wenn
    das Format unerwartet ist.

    Args:
        daten (Dict): Das Dictionary, das aus der JSON-Datei geladen wurde.

    Returns:
        Union[Dict, None]: Ein Dictionary mit den extrahierten Daten, oder None, wenn die Struktur nicht passt.
    """
    if not isinstance(daten, dict):
        if daten is None:
            return {}
        else:
            return {"wert": daten} # Wrappe den Wert in ein Dictionary, um ihn einheitlich zu behandeln

    extrahierte_daten = {}
    for schluessel, wert in daten.items():
        if isinstance(wert, (dict, list)):
            # Rekursiver Aufruf für verschachtelte Strukturen
            verschachtelte_daten = extrahiere_daten(wert)
            if verschachtelte_daten: # Prüfe, ob etwas zurückkam
               for k, v in verschachtelte_daten.items():
                    extrahierte_daten[f"{schluessel}_{k}"] = v
        else:
            extrahierte_daten[schluessel] = wert
    return extrahierte_daten


def verarbeite_ordner(ordner_pfad: str) -> pd.DataFrame:
    """
    Verarbeitet alle JSON-Dateien in einem Ordner und gibt ein kombiniertes DataFrame zurück.
    Diese Funktion sucht nach Dateien im Format "replay_data_[id]_[number].json".

    Args:
        ordner_pfad (str): Der Pfad zum Ordner, der die JSON-Dateien enthält.

    Returns:
        pd.DataFrame: Ein Pandas DataFrame, das aus den Daten aller passenden JSON-Dateien im Ordner erstellt wurde.
                      Gibt ein leeres DataFrame zurück, wenn keine Daten verarbeitet werden konnten.
    """
    pfad = Path(ordner_pfad)
    if not pfad.is_dir():
        print(f"Fehler: Der Pfad '{ordner_pfad}' ist kein gültiger Ordner.")
        return pd.DataFrame()  # Leeres DataFrame zurückgeben

    daten_liste: List[Dict] = []
    for datei_pfad in pfad.glob("replay_data_*.json"):  # Geht nur Dateien durch, die mit "replay_data_" beginnen und auf ".json" enden
        datei_inhalt = lese_json_datei(str(datei_pfad))
        if datei_inhalt:  # Nur fortfahren, wenn das JSON erfolgreich gelesen wurde
            extrahierte_daten = extrahiere_daten(datei_inhalt)
            if extrahierte_daten:
                # Füge die Daten der Liste hinzu, zusammen mit dem Dateinamen als identifizierende Spalte.
                extrahierte_daten['dateiname'] = datei_pfad.name  # Speichert den Dateinamen
                daten_liste.append(extrahierte_daten)

    if not daten_liste:
        print(f"Keine verwertbaren JSON-Daten im Ordner '{ordner_pfad}' gefunden (oder keine im richtigen Format).")
        return pd.DataFrame()  # Leeres DataFrame zurückgeben

    return pd.DataFrame(daten_liste)



def verarbeite_alle_ordner(basis_pfad: str) -> pd.DataFrame:
    """
    Verarbeitet alle Unterordner eines gegebenen Basisordners und gibt ein kombiniertes DataFrame zurück.

    Args:
        basis_pfad (str): Der Pfad zum Basisordner, der die Unterordner enthält.

    Returns:
        pd.DataFrame: Ein Pandas DataFrame, das alle Daten aus allen Unterordnern enthält.
                      Gibt ein leeres DataFrame zurück, wenn keine Daten verarbeitet werden konnten.
    """
    basis_pfad_obj = Path(basis_pfad)
    if not basis_pfad_obj.is_dir():
        print(f"Fehler: Der Pfad '{basis_pfad}' ist kein gültiger Basisordner.")
        return pd.DataFrame()

    alle_daten = []
    for unterordner_pfad in basis_pfad_obj.iterdir():
        if unterordner_pfad.is_dir():
            df = verarbeite_ordner(str(unterordner_pfad)) # Ruft die Funktion auf, die Dateien im richtigen Format verarbeitet
            if not df.empty:
                alle_daten.append(df)

    if not alle_daten:
        print(f"Keine verwertbaren JSON-Daten in den Unterordnern von '{basis_pfad}' gefunden.")
        return pd.DataFrame()  # Leeres DataFrame zurückgeben

    return pd.concat(alle_daten, ignore_index=True)



# --- Hauptprogramm ---
if __name__ == "__main__":
    basis_ordner = "Replays/Replay Data"  # Ersetze dies durch deinen tatsächlichen Pfad
    alle_replay_daten_df = verarbeite_alle_ordner(basis_ordner) # Ändere den Namen der DataFrame-Variable

    if not alle_replay_daten_df.empty:
        print("Verarbeitung abgeschlossen. Das kombinierte DataFrame:")
        print(alle_replay_daten_df.head())
    else:
        print("Keine Daten zu verarbeiten.")


Keine verwertbaren JSON-Daten im Ordner 'Replays/Replay Data/76561199111638990_Adraxah' gefunden (oder keine im richtigen Format).
Keine verwertbaren JSON-Daten im Ordner 'Replays/Replay Data/76561199030909760_' gefunden (oder keine im richtigen Format).
Verarbeitung abgeschlossen. Das kombinierte DataFrame:
                                     id  \
0  16ad9f5b-f4bd-48f2-a5d7-b6275fed6948   
1  f2edf9d7-5e6c-47d9-825c-988f93eebf8d   
2  d1feaaa4-3660-4043-8112-0f274521e123   
3  abd5d213-05c9-4eef-9eb1-b10381643384   
4  efbb8a80-1566-4bf6-9e6f-737b8e0581ce   

                                                link  \
0  https://ballchasing.com/api/replays/16ad9f5b-f...   
1  https://ballchasing.com/api/replays/f2edf9d7-5...   
2  https://ballchasing.com/api/replays/d1feaaa4-3...   
3  https://ballchasing.com/api/replays/abd5d213-0...   
4  https://ballchasing.com/api/replays/efbb8a80-1...   

                       created  uploader_steam_id uploader_name  \
0  2024-12-03T16:23:20.9666

In [6]:
def zeige_dataframe_ungekuerzt(df: pd.DataFrame):
    """
    Zeigt ein Pandas DataFrame vollständig und ungekürzt an, sowohl in der Breite als auch in der Länge.

    Args:
        df (pd.DataFrame): Das anzuzeigende DataFrame.
    """
    # Temporär die Pandas-Optionen ändern, um alles anzuzeigen
    with pd.option_context('display.max_rows', 1, 
                           'display.max_columns', None,
                           'display.width', None):
        print(df)

zeige_dataframe_ungekuerzt(alle_replay_daten_df)

                                      id  \
0   16ad9f5b-f4bd-48f2-a5d7-b6275fed6948   
..                                   ...   

                                                 link  \
0   https://ballchasing.com/api/replays/16ad9f5b-f...   
..                                                ...   

                        created  uploader_steam_id uploader_name  \
0   2024-12-03T16:23:20.966649Z  76561198164643612          jlt.   
..                          ...                ...           ...   

                     uploader_profile_url  \
0   https://steamcommunity.com/id/jlt_rl/   
..                                    ...   

                                      uploader_avatar status  \
0   https://avatars.steamstatic.com/ec8d9c6c8a5c6d...     ok   
..                                                ...    ...   

                    rocket_league_id                        match_guid  \
0   D7DC7CC54C2FD50CEA673CAF1CC86532  FE7C43C611EFB191C11E4E9D5E677929   
..           

In [7]:
alle_replay_daten_df.describe()

team_size      duration  overtime_seconds        season  \
count  48933.000000  48933.000000       8541.000000  48935.000000   
mean       2.561809    340.199599         78.855169     16.529662   
std        0.673995     93.268333        135.404306      2.156981   
min        1.000000      1.000000          2.000000      1.000000   
25%        2.000000    319.000000         21.000000     16.000000   
50%        3.000000    350.000000         48.000000     17.000000   
75%        3.000000    374.000000         95.000000     18.000000   
max        4.000000   2598.000000       3447.000000     18.000000   

       min_rank_tier  min_rank_division  max_rank_tier  max_rank_division  \
count   34727.000000       33539.000000   34892.000000       32776.000000   
mean       18.948685           2.521542      19.626820           2.502868   
std         1.702238           1.064826       1.309731           1.061262   
min         1.000000           1.000000       9.000000           1.000000   
25%        18.000000           2.000000      19.000000           2.000000   
50%        19.000000           3.000000      20.000000           2.000000   
75%        20.000000           3.000000      20.000000           3.000000   
max        22.000000           4.000000      22.000000           4.000000   

       blue_stats_ball_possession_time  blue_stats_ball_time_in_side  ...  \
count                     48849.000000                  48889.000000  ...   
mean                        133.045974                    156.991100  ...   
std                          41.440553                     50.462656  ...   
min                           0.030000                      0.870000  ...   
25%                         117.790000                    132.400000  ...   
50%                         136.860000                    158.860000  ...   
75%                         151.440000                    183.040000  ...   
max                        1079.680000                   1509.060000  ...   

       orange_stats_movement_count_powerslide  \
count                            48935.000000   
mean                               143.531971   
std                                 67.033857   
min                                  0.000000   
25%                                 99.000000   
50%                                138.000000   
75%                                183.000000   
max                               1617.000000   

       orange_stats_positioning_time_defensive_third  \
count                                   48935.000000   
mean                                      389.924051   
std                                       155.079043   
min                                         0.000000   
25%                                       292.414990   
50%                                       377.330000   
75%                                       488.765000   
max                                      4071.410000   

       orange_stats_positioning_time_neutral_third  \
count                                 48935.000000   
mean                                    267.247214   
std                                     104.516805   
min                                       0.000000   
25%                                     207.349995   
50%                                     261.030000   
75%                                     331.935000   
max                                    3038.450000   

       orange_stats_positioning_time_offensive_third  \
count                                   48935.000000   
mean                                      176.094808   
std                                        88.132299   
min                                         0.000000   
25%                                       128.560000   
50%                                       170.320000   
75%                                       218.435000   
max                                      3338.220000   

       orange_stats_positioning_time_defensive_half  \
count 

In [8]:
alle_replay_daten_df.head(1).to_csv('head.csv', index=False)

In [13]:
features = alle_replay_daten_df.columns

In [10]:
alle_replay_daten_df.head()

id  \
0  16ad9f5b-f4bd-48f2-a5d7-b6275fed6948   
1  f2edf9d7-5e6c-47d9-825c-988f93eebf8d   
2  d1feaaa4-3660-4043-8112-0f274521e123   
3  abd5d213-05c9-4eef-9eb1-b10381643384   
4  efbb8a80-1566-4bf6-9e6f-737b8e0581ce   

                                                link  \
0  https://ballchasing.com/api/replays/16ad9f5b-f...   
1  https://ballchasing.com/api/replays/f2edf9d7-5...   
2  https://ballchasing.com/api/replays/d1feaaa4-3...   
3  https://ballchasing.com/api/replays/abd5d213-0...   
4  https://ballchasing.com/api/replays/efbb8a80-1...   

                       created  uploader_steam_id uploader_name  \
0  2024-12-03T16:23:20.966649Z  76561198164643612          jlt.   
1  2025-02-17T18:03:45.362997Z  76561198277542361      Pineappl   
2   2025-04-14T21:45:54.05134Z  76561199252942548            jj   
3  2024-12-11T16:22:27.998595Z  76561198297750790        nicnic   
4  2025-02-06T16:46:54.013424Z  76561199681111411       Ryan099   

                                uploader_profile_url  \
0              https://steamcommunity.com/id/jlt_rl/   
1  https://steamcommunity.com/profiles/7656119827...   
2  https://steamcommunity.com/profiles/7656119925...   
3     https://steamcommunity.com/id/gorillaballen69/   
4  https://steamcommunity.com/profiles/7656119968...   

                                     uploader_avatar status  \
0  https://avatars.steamstatic.com/ec8d9c6c8a5c6d...     ok   
1  https://avatars.steamstatic.com/027654fa1a48cc...     ok   
2  https://avatars.steamstatic.com/fef49e7fa7e199...     ok   
3  https://avatars.steamstatic.com/8537685f9b6f02...     ok   
4  https://avatars.steamstatic.com/fef49e7fa7e199...     ok   

                   rocket_league_id                        match_guid  ...  \
0  D7DC7CC54C2FD50CEA673CAF1CC86532  FE7C43C611EFB191C11E4E9D5E677929  ...   
1  591E3F3041988E84557491A31BD5F874  8C2D2C3811EFED587ABA1BA3E3DA7507  ...   
2  4B8B391542A3CD06726FB190DD929DCC  F967631211F019789BD8A0A5B6670E51  ...   
3  F4A8ACD14D28827C9A315CA72AD044B3  96923E0011EFB7DB0FD71D991B760370  ...   
4  10C631F54D10E3529E85B8B59AD4B63B  199A3B2811EFE4A9A4D54C91381B22F2  ...   

  orange_stats_demo_inflicted orange_stats_demo_taken   playlist_name  \
0                           0                       1  Ranked Doubles   
1                           2                       2    Ranked Duels   
2                           1                       3  Ranked Doubles   
3                           0                       2  Ranked Doubles   
4                           0                       0  Ranked Doubles   

               map_name       server_name  server_region  \
0  DFH Stadium (Stormy)   EU716-Burnout11             EU   
1     Mannfield (Night)  EU774-Telemetry7             EU   
2       Champions Field   EU508-Renegade8             EU   
3              Aquadome     EU527-Apogee5             EU   
4         Beckwith Park  EU750-Marauder11             EU   

                               dateiname  blue_name  orange_name recorder  
0  replay_data_76561199013541842_42.json        NaN          NaN      NaN  
1  replay_data_76561199013541842_15.json        NaN          NaN      NaN  
2   replay_data_76561199013541842_3.json        NaN          NaN      NaN  
3  replay_data_76561199013541842_39.json        NaN          NaN      NaN  
4  replay_data_76561199013541842_19.json        NaN          NaN      NaN  

[5 rows x 144 columns]

In [11]:
def plot_verteilung(df: pd.DataFrame, titel: str):
    """
    Erstellt und speichert einen Boxplot und einen kombinierten Barplot mit KDE für alle numerischen Spalten
    in einem DataFrame.

    Args:
        df (pd.DataFrame): Der DataFrame, der die zu visualisierenden Daten enthält.
        titel (str): Ein Titel für die generierten Plots.
    """
    numerische_spalten = df.select_dtypes(include=['number']).columns
    anzahl_spalten = len(numerische_spalten)
    if anzahl_spalten == 0:
        print(f"Keine numerischen Spalten zum Plotten im DataFrame für '{titel}'.")
        return

    # Boxplots erstellen
    plt.figure(figsize=(15, 5 * anzahl_spalten))  # Dynamische Höhe basierend auf der Anzahl der Spalten
    plt.suptitle(f"Verteilungsplots (Boxplots) für: {titel}", fontsize=16)
    for i, spalte in enumerate(numerische_spalten):
        plt.subplot(anzahl_spalten, 1, i + 1)
        sns.boxplot(data=df[spalte], orient='h')
        plt.title(spalte)
    plt.tight_layout(rect=[0, 0.03, 1, 0.95])  # Platz für den Gesamttitel
    plt.savefig(f"{titel}_boxplots.png")
    plt.close()

    # Barplots mit KDE erstellen
    plt.figure(figsize=(15, 5 * anzahl_spalten))
    plt.suptitle(f"Verteilungsplots (Barplots mit KDE) für: {titel}", fontsize=16)
    for i, spalte in enumerate(numerische_spalten):
        plt.subplot(anzahl_spalten, 1, i + 1)
        sns.histplot(data=df, x=spalte, kde=True)
        plt.title(spalte)
    plt.tight_layout(rect=[0, 0.03, 1, 0.95])
    plt.show()
plot_verteilung(alle_replay_daten_df, "Alle Replay Daten")

In [15]:
for i in features:
    print(i)

id
link
created
uploader_steam_id
uploader_name
uploader_profile_url
uploader_avatar
status
rocket_league_id
match_guid
title
map_code
match_type
team_size
playlist_id
duration
overtime
overtime_seconds
season
season_type
date
date_has_timezone
visibility
min_rank_id
min_rank_tier
min_rank_division
min_rank_name
max_rank_id
max_rank_tier
max_rank_division
max_rank_name
groups_wert
blue_color
blue_players_wert
blue_stats_ball_possession_time
blue_stats_ball_time_in_side
blue_stats_core_shots
blue_stats_core_shots_against
blue_stats_core_goals
blue_stats_core_goals_against
blue_stats_core_saves
blue_stats_core_assists
blue_stats_core_score
blue_stats_core_shooting_percentage
blue_stats_boost_bpm
blue_stats_boost_bcpm
blue_stats_boost_avg_amount
blue_stats_boost_amount_collected
blue_stats_boost_amount_stolen
blue_stats_boost_amount_collected_big
blue_stats_boost_amount_stolen_big
blue_stats_boost_amount_collected_small
blue_stats_boost_amount_stolen_small
blue_stats_boost_count_collected